---
toc: false
page-layout: full
---

# Week 4B: Interactive Web Maps

- Section 401
- Wednesday, September 27, 2023

In [53]:
import geopandas as gpd
import pandas as pd

## Interactive maps in Python

Haven't we already done this?

**Yes!** So far, we've used hvplot, geopandas, & altair to create interactive map-based visualizations.

## Why do we need something more?

<img src="imgs/leaflet-logo.png" width=500></img>

[Leaflet documentation](https://leafletjs.com/)

## The benefits of Leaflet

- The leading open-source mapping library
- Simple and powerful
- Leverage the open-source community and lots of powerful plugins

## Folium: Leaflet in Python

**Pros**
- Create Leaflet.js maps directly from Python
- Combine power of Leaflet.js with the data wrangling ease of Python

**Cons**
- A wrapper for **most, but not all** of Leaflet's functionality
- Can be difficult to debug and find errors


::: {.callout-note title="Reference"}
Check out the [Folium docs](https://python-visualization.github.io/folium/latest/index.html) for more info.
:::

## We've already seen choropleth maps with Folium

The geopandas `.explore()` function, which makes interactive choropleth maps, produces Folium maps!

Let's load the median property assessment data by neighborhood from last lecture's exercise:

In [444]:
# Load the data from a CSV file into a pandas DataFrame
trash_requests_df = pd.read_csv(
    "data/trash_311_requests_2020.csv",  # Use the file path relative to the current folder
)

# Remove rows with missing geometry
trash_requests_df = trash_requests_df.dropna(subset=["lat", "lon"])


# Create our GeoDataFrame with geometry column created from lon/lat
trash_requests = gpd.GeoDataFrame(
    trash_requests_df,
    geometry=gpd.points_from_xy(trash_requests_df["lon"], trash_requests_df["lat"]),
    crs="EPSG:4326",
)

Load neighborhoods and do the spatial join to associate a neighborhood with each ticket:

In [445]:
# Load the neighborhoods
neighborhoods = gpd.read_file("data/zillow_neighborhoods.geojson")

# Do the spatial join to add the "ZillowName" column
requests_with_hood = gpd.sjoin(
    trash_requests,
    neighborhoods.to_crs(trash_requests.crs),
    predicate="within",
)

Group by neighborhood, calculate the number of tickets per neighborhood, and then merge neighborhood geometries.

In [446]:
requests_by_hood = pd.merge(
    # GeoDataFrame is left
    neighborhoods,
    # DataFrame is right: This is the number of tickets per neighborhood
    requests_with_hood.groupby("ZillowName", as_index=False).size(),
    # Merge column,
    on="ZillowName",
).rename(
    # Rename size column
    columns={"size": "num_tickets"}
)

# Get the area of each geometry in sq. meters
# NOTE: we are converting to EPSG:3857 which has units of meters
area = requests_by_hood.to_crs(epsg=3857).geometry.area


# Normalize by area
requests_by_hood["num_tickets_per_area"] = requests_by_hood["num_tickets"] / area * 1e4

In [447]:
requests_by_hood.head()

ZillowName                                           geometry  \
0   Academy Gardens  POLYGON ((-74.99851 40.06435, -74.99456 40.061...   
1    Allegheny West  POLYGON ((-75.16592 40.00327, -75.16596 40.003...   
2           Andorra  POLYGON ((-75.22463 40.06686, -75.22588 40.065...   
3  Aston Woodbridge  POLYGON ((-75.00860 40.05369, -75.00861 40.053...   
4   Bartram Village  POLYGON ((-75.20733 39.93350, -75.20733 39.933...   

   num_tickets  num_tickets_per_area  
0           84              0.350561  
1          330              0.646749  
2           83              0.212905  
3          110              0.486609  
4           35              0.155914

The `.explore()` function is a wrapper around Folium/leaflet.js

In [448]:
m = requests_by_hood.explore(column="num_tickets_per_area", tiles="Cartodb positron")

m

The object returned by `.explore()` a Folium map!

In [182]:
type(m)

folium.folium.Map

### The explore() function

The `.explore()` function is a powerful wrapper around folium with a lot of the same functionality of the `plot()` function in geopandas. In my experience, it is much easier to work with than folium directly. My recommendation is to use the `.explore()` function when you can.

#### Classification schemes

You can use the same classification schemes to bin your data when using the `explore()` function. For example:

In [243]:
m = requests_by_hood.explore(
    column="num_tickets_per_area",
    tiles="Cartodb positron",
    scheme="FisherJenks",  # NEW: the classification scheme
    k=5,  # NEW: the number of bins
)

m

#### Style options

The `explore()` function allows you to specify dictionaries with style keywords for the GeoJSON. The allowed options come directly from the leaflet.js library. Check out the documentation for the `.explore()` function for more info. You can see the allowed values for GeoJSON on the [leaflet documentation](https://leafletjs.com/reference.html#path-option).

For example, let's plot our neighborhood GeoJSON and apply a default style, as well as as a style for when the user hover (highlights) a polygon.

In [193]:
m = hoods.explore(
    tiles="Cartodb dark matter",
    # NEW: The style dictionary
    style_kwds={
        "weight": 2,
        "color": "lightblue",
        "fillOpacity": 0.1,
    },
    highlight=True,  # NEW: turn on highlighting
    # NEW: The style dict to apply when hovering
    highlight_kwds={
        "weight": 2,
        "color": "red",
    },
)

m

You can also perform styling via functions that take in a GeoJSON feature and return a dictionary of style options. This allows you to style GeoJSON features differently based on the `.properties` attribute of the GeoJSON feature.

For example:


In [217]:
def my_style_function(feature):
    """Change the style based on whether the number of tickets > 500."""

    # Data attributes stored in properties dict
    properties = feature["properties"]

    # Shared style
    style = {"weight": 2, "fillOpacity": 0.8, "color": "white"}

    # Change fillColor
    if properties["num_tickets"] > 500:
        style["fillColor"] = "red"
    else:
        style["fillColor"] = "lightblue"

    # Return style dict
    return style

In [218]:
m = requests_by_hood.explore(
    tiles="Cartodb dark matter",
    style_kwds={"style_function": my_style_function},  # NEW: The style function
)

m

## More Folium features

We'll cover a few more of the key features of Folium today...

**Things we'll cover:**
1. Creating a base map with tiles
1. Overlaying GeoJSON features with layer control
1. Examples of Folium plugins

In [170]:
import folium

### 1. Creating a Folium map

**Key function:** `folium.Map`

#### Lots of configuration options

Some key ones: 
- **location**: the center location of the map
- **zoom_start**: the initial zoom level of the map
- **tiles**: the name of the tile provider 

Let's take a look at the help message:

In [147]:
folium.Map?

Init signature:
folium.Map(
    location=None,
    width='100%',
    height='100%',
    left='0%',
    top='0%',
    position='relative',
    tiles='OpenStreetMap',
    attr=None,
    min_zoom=0,
    max_zoom=18,
    zoom_start=10,
    min_lat=-90,
    max_lat=90,
    min_lon=-180,
    max_lon=180,
    max_bounds=False,
    crs='EPSG3857',
    control_scale=False,
    prefer_canvas=False,
    no_touch=False,
    disable_3d=False,
    png_enabled=False,
    zoom_control=True,
    **kwargs,
)
Docstring:     
Create a Map with Folium and Leaflet.js

Generate a base map of given width and height with either default
tilesets or a custom tileset URL. The following tilesets are built-in
to Folium. Pass any of the following to the "tiles" keyword:

    - "OpenStreetMap"
    - "Mapbox Bright" (Limited levels of zoom for free tiles)
    - "Mapbox Control Room" (Limited levels of zoom for free tiles)
    - "Stamen" (Terrain, Toner, and Watercolor)
    - "Cloudmade" (Must pass API key)
    - "Mapb

#### The default tiles: OpenStreetMap

In [285]:
# let's center the map on Philadelphia
m = folium.Map(location=[39.99, -75.13], zoom_start=11)

m

In [328]:
m = folium.Map(location=[39.99, -75.13], zoom_start=11, tiles="StamenWaterColor")

m

#### Other tile providers

Check out the `xyzservices.providers` for all of the available options. You can pass any of these built-in tile providers to `Folium.Map()` or the `.explore()` function.

::: {.callout-tip}
Here is a very useful demo of common tile providers: https://leaflet-extras.github.io/leaflet-providers/preview
:::

In [286]:
import xyzservices

In [292]:
xyzservices.providers

{'OpenStreetMap': {'Mapnik': {'url': 'https://tile.openstreetmap.org/{z}/{x}/{y}.png',
   'max_zoom': 19,
   'html_attribution': '&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors',
   'attribution': '(C) OpenStreetMap contributors',
   'name': 'OpenStreetMap.Mapnik'},
  'DE': {'url': 'https://tile.openstreetmap.de/{z}/{x}/{y}.png',
   'max_zoom': 18,
   'html_attribution': '&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors',
   'attribution': '(C) OpenStreetMap contributors',
   'name': 'OpenStreetMap.DE'},
  'CH': {'url': 'https://tile.osm.ch/switzerland/{z}/{x}/{y}.png',
   'max_zoom': 18,
   'html_attribution': '&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors',
   'attribution': '(C) OpenStreetMap contributors',
   'bounds': [[45, 5], [48, 11]],
   'name': 'OpenStreetMap.CH'},
  'France': {'url': 'https://{s}.tile.openstreetmap.fr/osmfr/{z}/{x}/{y}.png',
   'max_zoom': 20,
   'html_attribution': '&copy; OpenStreetMap France | &copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors',
   'attribution': '(C) OpenStreetMap France | (C) OpenStreetMap contributors',
   'name': 'OpenStreetMap.France'},
  'HOT': {'url': 'https://{s}.tile.openstreetmap.fr/hot/{z}/{x}/{y}.png',
   'max_zoom': 19,
   'html_attribution': '&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors, Tiles style by <a href="https://www.hotosm.org/" target="_blank">Humanitarian OpenStreetMap Team</a> hosted by <a href="https://openstreetmap.fr/" target="_blank">OpenStreetMap France</a>',
   'attribution': '(C) OpenStreetMap contributors, Tiles style by Humanitarian OpenStreetMap Team hosted by OpenStreetMap France',
   'name': 'OpenStreetMap.HOT'},
  'BZH': {'url': 'https://tile.openstreetmap.bzh/br/{z}/{x}/{y}.png',
   'max_zoom': 19,
   'html_attribution': '&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors, Tiles courtesy of <a href="http://www.openstreetmap.bzh/" target="_blank">Breton OpenStreetMap Team</a>',
   'attribution': '(C) OpenStreetMap contributors, Tiles courtesy of Breton OpenStreetMap Team',
   'bounds': [[46.2, -5.5], [50, 0.7]],
   'name': 'OpenStreetMap.BZH'},
  'BlackAndWhite': {'url': 'http://{s}.tiles.wmflabs.org/bw-mapnik/{z}/{x}/{y}.png',
   'max_zoom': 18,
   'attribution': '(C) OpenStreetMap contributors',
   'html_attribution': '&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors',
   'name': 'OpenStreetMap.BlackAndWhite'}},
 'MapTilesAPI': {'OSMEnglish': {'url': 'https://maptiles.p.rapidapi.com/{variant}/{z}/{x}/{y}.png?rapidapi-key={apikey}',
   'html_attribution': '&copy; <a href="http://www.maptilesapi.com/">MapTiles API</a>, &copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors',
   'attribution': '(C) MapTiles API, (C) OpenStreetMap contributors',
   'variant': 'en/map/v1',
   'apikey': '<insert your api key here>',
   'max_zoom': 19,
   'name': 'MapTilesAPI.OSMEnglish'},
  'OSMFrancais': {'url': 'https://maptiles.p.rapidapi.com/{variant}/{z}/{x}/{y}.png?rapidapi-key={apikey}',
   'html_attribution': '&copy; <a href="http://www.maptilesapi.com/">MapTiles API</a>, &copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors',
   'attribution': '(C) MapTiles API, (C) OpenStreetMap contributors',
   'variant': 'fr/map/v1',
   'apikey': '<insert your api key here>',
   'max_zoom': 19,
   'name': 'MapTilesAPI.OSMFrancais'},
  'OSMEspagnol': {'url': 'https://maptiles.p.rapidapi.com/{variant}/{z}/{x}/{y}.png?rapidapi-key={apikey}',
   'html_attribution': '&copy; <a href="http://www.maptilesapi.com/">MapTiles API</a>, &copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors',
   'attribution': '(C) MapTiles API, (C) OpenStreetMap contributors',
   'variant': 'es/map/v1',
   'apikey': '<insert 

Let's try out a couple of examples:

USGS Topo:

In [325]:
m = folium.Map(
    location=[39.99, -75.13], zoom_start=11, tiles=xyzservices.providers.USGS.USTopo
)

m

Esri National Geographic World Map:

In [333]:
m = folium.Map(
    location=[39.99, -75.13],
    zoom_start=11,
    tiles=xyzservices.providers.Esri.NatGeoWorldMap,
)

m

CartoDB Dark Matter:

In [334]:
m = folium.Map(
    location=[39.99, -75.13],
    zoom_start=11,
    tiles=xyzservices.providers.CartoDB.DarkMatter,
)

m

### 2. Overlaying multiple GeoJSON layers on a folium map

The `.explore()` function can handle points in addition to polygon geometry objects. And you can layer multiple types of GeoJSON on the same folium map, and add a widget to control which layers are active on the map.


As an example, we'll keep exploring our trash-related 311 ticket dataset. Let's take a look at the top 10 neighborhoods in terms of the number of tickets per neighborhood area:

In [335]:
requests_by_hood.sort_values(by="num_tickets_per_area", ascending=False).head(n=10)

ZillowName                                           geometry  \
57           Greenwich  POLYGON ((-75.15294 39.92465, -75.15342 39.922...   
31       East Passyunk  POLYGON ((-75.16971 39.92442, -75.16835 39.930...   
86             Newbold  POLYGON ((-75.16971 39.92442, -75.17023 39.921...   
72   Lower Moyamensing  POLYGON ((-75.15660 39.92271, -75.15827 39.915...   
5          Bella Vista  POLYGON ((-75.15865 39.94277, -75.15757 39.942...   
25              Dunlap  POLYGON ((-75.22457 39.96492, -75.21995 39.963...   
139      West Passyunk  POLYGON ((-75.18528 39.93020, -75.17533 39.928...   
108       Point Breeze  POLYGON ((-75.18495 39.94013, -75.17622 39.939...   
103          Pennsport  POLYGON ((-75.14531 39.93361, -75.14532 39.933...   
142            Whitman  POLYGON ((-75.14766 39.91674, -75.14825 39.913...   

     num_tickets  num_tickets_per_area  
57           214              6.781077  
31           648              6.222775  
86           525              5.712863  
72           881              5.366825  
5            416              5.082199  
25           189              4.983522  
139          495              4.888462  
108         1154              4.308334  
103          447              4.062493  
142          476              3.983558

The Greenwich neighborhood has the highest number of tickets per area, but a relatively low number of overall tickets. Let's take a look at the tickets in closer detail.

In [336]:
# Extract out the point tickets for Greenwich
greenwich_tickets = requests_with_hood.query("ZillowName == 'Greenwich'")

In [340]:
# Get the neighborhood boundary for Greenwich
greenwich_geo = neighborhoods.query("ZillowName == 'Greenwich'")

::: {.callout-note}

If you are using the `.explore()` function in geopandas, you if you have an existing Folium map, you can pass it to the `explore()` function using the `m=` keyword. See the [docs](https://geopandas.org/en/stable/docs/reference/api/geopandas.GeoDataFrame.explore.html) for more info.

:::

In [350]:
# Plot the neighborhood boundary
m = greenwich_geo.explore(
    style_kwds={"weight": 4, "color": "black", "fillColor": "none"},
    name="Neighborhood boundary",
    tiles=xyzservices.providers.CartoDB.Voyager,
)


# Add the individual tickets as circle markers and style them
greenwich_tickets.explore(
    m=m,  # Add to the existing map!
    marker_kwds={"radius": 7, "fill": True, "color": "crimson"},
    marker_type="circle_marker", # or 'marker' or 'circle'
    name="Tickets",
)

# Hse folium to add layer control
folium.LayerControl().add_to(m)

m  # show map

Interesting! There are definitely *spatial* clusters of 311 tickets, e.g., hot spots. But these tickets are from *all* of 2020...

**Question:** I wonder if they were clustered in *time* as well as space, e.g., a large number of tickets in a short period of time. This could be indicative of a couple bad weeks of trash collections, and a few "power users" putting in lots of repeat 311 tickets to the City if the issue was resolved. 

Let's use the folium/leaflet plugin ecosystem to try to answer this question!

### 3. Leaflet/Folium plugins

One of leaflet's strengths: a rich set of open-source plugins

https://leafletjs.com/plugins.html

Many of these are available in Folium! Check out the [plugins gallery](https://python-visualization.github.io/folium/latest/user_guide/plugins.html) on the folium documentation for examples.

#### 3A. Time-stamped GeoJSON

The `folium.plugins.TimestampedGeoJson()` object can plot a GeoJSON collection over time, adding a slider to control what time frame is currently shown.

Let's use this to examine the trends in tickets in Greenwich by month in 2020...


::: {.callout-note title="Notes"}

There's a few things we'll need to do to prepare:

- Add a "time" column that includes the datetime for each point. We can rename our "requested_datetime" column. 
- Pass in GeoJSON to the function, not the GeoDataFrame. We can use the `.to_json()` function to convert.
- Choose a time period to show on the slider, e.g., how many time slices to show. We will use a monthly interval below.

:::

In [431]:
# Select only the two columns we need and rename to "time"
ticket_timestamps = (
    greenwich_tickets[["requested_datetime", "geometry"]]
    .rename(columns={"requested_datetime": "time"})
)

In [432]:
# Plot the neighborhood boundary first
m = greenwich_geo.explore(
    style_kwds={"weight": 4, "color": "black", "fillColor": "none"},
    name="Neighborhood boundary",
    tiles=xyzservices.providers.CartoDB.Voyager,
)

# Add the time-stamped GeoJSON
folium.plugins.TimestampedGeoJson(
    ticket_timestamps.to_json(),  # Convert to GeoJSON
    period="P1M",  # Show the data in one month intervals
    duration="P1M",  # Only show points for 1 month and then remove them
    auto_play=False,  # Don't start playing by default
    loop=False,  # Loop the animation
    max_speed=1,  # Max frame speed
    loop_button=True,  # Show a loop button
    transition_time=500,  # Time between frames in ms
).add_to(m)

m

Ah! The summer months, July and August in particular, saw a lot of requests, just as we saw before with the citywide data! By September or October the number of tickets declines, showing that the trash-related problems were a short-term issue.

::: {.callout-note title="Deep dive: Styling the markers"}

*A brief deep dive, feel free to keep moving!* 

Styling the markers in this case is much harder to do than when we were working with the `.explore()` function. We need to add the style dictionary we want as a attribute of each feature's property dictionary. So we'll need to convert to a GeoJSON dict, and then manually loop over each feature and add the style we want.

The example below really illustrates how `.explore()` is often the best option for its ease of use!

:::

The `.to_json()` function returns a string version of the GeoJSON dict. We can parse it into a Python dict by using the `json.loads()` function.

In [433]:
import json

In [436]:
# This is our GeoJSON points as a dict
geosjon_dict = json.loads(ticket_timestamps.to_json())

In [437]:
geosjon_dict

{'type': 'FeatureCollection',
 'features': [{'id': '842',
   'type': 'Feature',
   'properties': {'time': '2020-01-06 10:42:43'},
   'geometry': {'type': 'Point',
    'coordinates': [-75.155657471, 39.923776419]}},
  {'id': '1168',
   'type': 'Feature',
   'properties': {'time': '2020-07-13 21:30:03'},
   'geometry': {'type': 'Point',
    'coordinates': [-75.153858572, 39.924485692]}},
  {'id': '1171',
   'type': 'Feature',
   'properties': {'time': '2020-03-05 17:35:06'},
   'geometry': {'type': 'Point',
    'coordinates': [-75.160990158, 39.924627016]}},
  {'id': '1172',
   'type': 'Feature',
   'properties': {'time': '2020-03-05 13:15:21'},
   'geometry': {'type': 'Point',
    'coordinates': [-75.160990158, 39.924627016]}},
  {'id': '1183',
   'type': 'Feature',
   'properties': {'time': '2020-03-27 14:22:31'},
   'geometry': {'type': 'Point',
    'coordinates': [-75.155498831, 39.924592881]}},
  {'id': '1467',
   'type': 'Feature',
   'properties': {'time': '2020-01-03 14:18:31'},


Now loop over each feature and add the style:

In [438]:
for feature in geosjon_dict["features"]:
    
    # Use a circle for each icon
    feature["properties"]["icon"] = "circle"
    
    # Style the circles
    feature["properties"]["style"] = {"radius": 10, "fill": True, "color": "crimson"}

In [441]:
# Plot the neighborhood boundary first
m = greenwich_geo.explore(
    style_kwds={"weight": 4, "color": "black", "fillColor": "none"},
    name="Neighborhood boundary",
    tiles=xyzservices.providers.CartoDB.Voyager,
)

# Add the time-stamped GeoJSON
folium.plugins.TimestampedGeoJson(
    geosjon_dict,  # NEW: use the styled GeoJSON
    period="P1M",
    duration="P1M",
    auto_play=False,
    loop=False,
    max_speed=1,
    loop_button=True,
    transition_time=500,
).add_to(m)

m

#### 3B. Heatmaps


In [460]:
folium.plugins.HeatMap?

Init signature:
folium.plugins.HeatMap(
    data,
    name=None,
    min_opacity=0.5,
    max_zoom=18,
    radius=25,
    blur=15,
    gradient=None,
    overlay=True,
    control=True,
    show=True,
    **kwargs,
)
Docstring:     
Create a Heatmap layer

Parameters
----------
data : list of points of the form [lat, lng] or [lat, lng, weight]
    The points you want to plot.
    You can also provide a numpy.array of shape (n,2) or (n,3).
name : string, default None
    The name of the Layer, as it will appear in LayerControls.
min_opacity  : default 1.
    The minimum opacity the heat will start at.
max_zoom : default 18
    Zoom level where the points reach maximum intensity (as intensity
    scales with zoom), equals maxZoom of the map by default
radius : int, default 25
    Radius of each "point" of the heatmap
blur : int, default 15
    Amount of blur
gradient : dict, default None
    Color gradient config. e.g. {0.4: 'blue', 0.65: 'lime', 1: 'red'}
overlay : bool, default True
  

In [464]:
coords = greenwich_tickets[['lat', 'lon']]

In [465]:
# Plot the neighborhood boundary first
m = greenwich_geo.explore(
    style_kwds={"weight": 4, "color": "black", "fillColor": "none"},
    name="Neighborhood boundary",
    tiles=xyzservices.providers.CartoDB.Voyager,
)

# Add heat map coordinates
folium.plugins.HeatMap(coords.values, radius=20).add_to(m)

# Show map
m

#### 3C: Marker clusters

**Question:** Can we visualize all tickets citywide in 2020 at once? 

In [489]:
len(trash_requests)

47690

Let's try the heat map plugin:

In [491]:
# let's center the map on Philadelphia
m = folium.Map(
    location=[39.99, -75.13], zoom_start=11, tiles=xyzservices.providers.CartoDB.Voyager
)

# All coords
coords = trash_requests[["lat", "lon"]] # Remember, (lat, lon) order

# Add heat map coordinates
folium.plugins.HeatMap(coords.values, radius=20).add_to(m)

# Show map
m

...Not great! There are too many points to properly visualize all of the data at once.

Instead, let's check out `folium.plugins.FastMarkerCluster()`. This plugin clusters the data automatically for each zoom level, and can easily handle thousands of points at once without crashing your browser. 



In [487]:
# let's center the map on Philadelphia
m = folium.Map(
    location=[39.99, -75.13], zoom_start=11, tiles=xyzservices.providers.CartoDB.DarkMatter
)


folium.plugins.FastMarkerCluster(data=coords).add_to(m)

m

::: {.callout-note title='Reminder'}

Check out the [plugins gallery](https://python-visualization.github.io/folium/latest/user_guide/plugins.html) on the folium documentation for the available plugins and examples for each.

:::

## That's it!

- See you next week for more geospatial analysis
- We'll dive into urban street networks and raster data